In [ ]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets

## Read in Measurements

In [ ]:
two_k_sampling_trafo = pd.read_csv(r'2000OhmSamplingTrafoSupply.csv')
one_k_sampling_trafo = pd.read_csv(r'1000OhmSamplingTrafoSupply.csv')
temperature_measurement = pd.read_csv(r'TempSamplingTrafoSupply.csv')
constant_sampling = pd.read_csv(r'1000OhmSampling.csv')

# Calculation Function for $\vartheta(R_{PT1000})$
$\vartheta(R_{PT1000}) = \frac{-\alpha R_0 + \sqrt{\alpha^2R_0^2 - 4\beta R_0 \left(R_0 - R_{PT1000}\right)}}{2\beta R_0}$

with
* $\alpha = 3.9083 \cdot 10^{-3}$
* $\beta = -5.7750 \cdot 10^{-7}$
* $R_0 = 1000~\Omega$

In [ ]:
R_zero = 1000.0
A = 3.9083E-3
B = -5.7750E-7

def calc_temp(resistance):
    temp = (-R_zero * A + np.sqrt(R_zero*R_zero * A * A - 4* R_zero * B * (R_zero - resistance)))/(2*R_zero*B)
    return temp

## Description of ADC Value

In [ ]:
print(constant_sampling['adc_results.pa2_raw'].describe())

--------------------
# Calculate Temperature from Resistance Value

In [ ]:
df_list = [one_k_sampling_trafo, two_k_sampling_trafo, temperature_measurement, constant_sampling]
for df in df_list:
    df['temp_calculated'] = df.apply(lambda row: calc_temp(row['ext_lf_corr']) , axis=1)


# Histograms -- Starting from Index 100

In [ ]:
fig, axes = plt.subplots(nrows=3, ncols=3, figsize=(28,15))
plot_data = [(one_k_sampling_trafo, '1 kOhm Sampling Transformer powered', 0), (two_k_sampling_trafo, '2 kOhm Sampling Transformer powered' , 0), (constant_sampling, '1 kOhm Sampling', 100)]
signal_list = [('adc_results.pa2_raw', 20), ('ext_lf_corr', 20), ('temp_calculated', 20)]

for (data_df, title, start_idx), ax_rows in zip(plot_data, axes):
    for ax,sig in zip(ax_rows, signal_list):
        n, bins, patches = ax.hist(data_df[sig[0]][start_idx:], sig[1], density=1)
        mu = np.mean(data_df[sig[0]][start_idx:])
        sigma = np.std(data_df[sig[0]][start_idx:])
        y = ((1 / (np.sqrt(2 * np.pi) * sigma)) * np.exp(-0.5 * (1 / sigma * (bins - mu))**2))
        ax.plot(bins, y)
        ax.set_title('Histogram of '+sig[0]+' for '+title)
plt.show()

# Startup of Moving Average Filter with $\alpha' = 0.005$

Filter difference equation: $y[n] = (1-\alpha')y[n-1] + \alpha'x[n]$

In [ ]:
fig, ax = plt.subplots(nrows=2, ncols=1, figsize=(28,6), sharex=True)
data = constant_sampling['ext_lf_corr'][:20]
ax[0].plot(constant_sampling['Time'][:20], data)
ax[1].plot(constant_sampling['Time'][:20], constant_sampling['temp_calculated'][:20])
plt.show()

# Temperature Plotting

In [ ]:
idx_count = len(temperature_measurement.index)
@interact(low=(0,idx_count -1,10), high=(0, idx_count-1, 10))
def plot_temp(low=0, high=idx_count-1):
    fig, ax = plt.subplots(nrows=3, ncols=1, figsize=(28,9*3), sharex=True)
    ax[0].plot(temperature_measurement['Time'][low:high], temperature_measurement['ext_lf_corr'][low:high])
    ax[1].plot(temperature_measurement['Time'][low:high], temperature_measurement['adc_results.pa2_raw'][low:high])
    ax[2].plot(temperature_measurement['Time'][low:high], temperature_measurement['temp_calculated'][low:high])
    plt.plot()